In [1]:

%load_ext autoreload
%autoreload 2
import xarray as xr
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import scipy
import datetime
import cartopy
import cartopy.crs as ccrs
import pickle
#import Tracking_Functions
from dateutil import relativedelta
import os

os.chdir('/work/aa0238/a271093/Scripts/')
import MOAAP.Tracking_Functions as Tracking_Functions
from MOAAP.DataLoader import * 
from MOAAP.utils import * 
from MOAAP.Corrections import * 

In [2]:
#data_path = '/work/aa0049/a271109/spice-v2.1/chain/work/polarres_wp3_cmip_CNRM/post/yearly/'

suffix = 'remapped_3x'
file_type = '.nc'
data_path = '/work/aa0238/a271093/data/Jan_runs/CNRM_control_remapped_3x/'
output_path = '/work/aa0238/a271093/results/MOAAP/IVT_Tracking/CNRM_control_test/'
threshold_file = '/work/aa0238/a271093/data/input/IVT_85_percentiles_CNMR_control_3dx3dy.nc'
first_year = 1985
last_year = 1986

start_date_list, end_date_list = create_datetime_lists(first_year,last_year) 
first_processed_date = start_date_list[0]
last_processed_date = end_date_list[-1]

In [3]:
#ds_ivt_pctl=xr.open_dataset('/work/aa0049/a271109/data_misc/AR_Guan/code/ivt_percentile_mlauer_removed-ens-lev_remapbilWP3domain.nc',decode_times=False)

#IVTtrheshold=ds_ivt_pctl.ivt1.values

ds_ivt_pctl=xr.open_dataset(threshold_file,decode_times=False)
IVTtrheshold=ds_ivt_pctl.IVT_85perc.values



dict_keys_offset = 0
for start_date, end_date in zip(start_date_list, end_date_list):
    
    IVTuLoader= DataLoader('IVTu', data_path, start_date, end_date,suffix=suffix, file_type = file_type)
    IVTvLoader= DataLoader('IVTv', data_path, start_date, end_date,suffix=suffix, file_type = file_type)

    IVTudata=IVTuLoader.load_datasets(rm_nc=False)
    IVTvdata=IVTvLoader.load_datasets(rm_nc=False)


    rLon = xr.broadcast(IVTudata.rlon, IVTudata.rlat)[0].values.T
    rLat = xr.broadcast(IVTudata.rlon, IVTudata.rlat)[1].values.T

    Lon = xr.broadcast(IVTudata.lon, IVTudata.lat)[0].values
    Lat = xr.broadcast(IVTudata.lon, IVTudata.lat)[1].values

    Mask=1*(rLat>-999)
    Time_sel = IVTuLoader.time_sel
    
    output_file_name_temp = f'MOAPP_ICON_control_CNRMforc_100and85controlperc_{suffix}'
    output_file_name = f'{output_file_name_temp}_{get_datetime_str(start_date)}-{get_datetime_str(end_date)}'

    

    Tracking_Functions.moaap(Lon = rLon,                           # 2Dlongitude grid centers
                              Lat = rLat,                           # 2D latitude grid spacing
                              Time = Time_sel,                         # datetime vector of data
                              dT = 1,                              # integer - temporal frequency of data [hour]
                              Mask = Mask,                         # mask with dimensions [lat,lon] defining analysis region

                              ivte = IVTudata.IVTu.values, # zonal integrated vapor transport [kg m-1 s-1]
                              ivtn = IVTvdata.IVTv.values, # meidional integrated vapor transport [kg m-1 s-1]
                              regular_Lon = Lon,
                              regular_Lat = Lat,
                              IVTtrheshold = IVTtrheshold, # Integrated water vapor transport threshold for AR detection [kg m-1 s-1]
                               # JLa: additionall fixed threshold 100 in code

                              DataName = output_file_name,
                              OutputFolder=output_path ,
                              dict_keys_offset = dict_keys_offset
                            )
                       
                             
    cleanup_dicts(output_path,
                  output_file_name_temp,
                  start_date,
                  end_date, 
                  last_processed_date,
                  type_='IVT'
                 )
        
    cleanup_dicts(output_path,
                  output_file_name_temp,
                  start_date,
                  end_date, 
                  last_processed_date,
                  type_='ARs'
                 )
    
    correct_nc_file(output_path,
                    output_file_name_temp, 
                    start_date,
                    end_date,
                    last_processed_date
                   )
                             
    dict_keys_offset +=5000

 
The provided variables allow tracking the following phenomena
 
|  phenomenon  | tracking |
---------------------------
   Jetstream   |   no
   PSL CY/ACY  |   no
   Z500 CY/ACY |   no
   COLs        |   no
   IVT ARs     |   yes
   MS ARs      |   no
   Fronts      |   no
   TCs         |   no
   MCSs        |   no
   Equ. Waves  |   no
---------------------------
 
======> track IVT streams and atmospheric rivers (ARs)
        3784 object found
        break up long living IVT objects that have many elements


 42%|████▏     | 302/715 [00:35<00:48,  8.47it/s]


KeyboardInterrupt: 

In [ ]:
with open('/work/aa0238/a271093/results/MOAAP/IVT_Tracking/CNRM_control_test/IVT_MOAPP_ICON_control_CNRMforc_100and85controlperc_remapped_3x_1984_01_01-1984_07_01_corrected.pkl', 'rb') as pickle_file:
    IVT1 = pickle.load(pickle_file)


Mergetime /work/aa0049/a271109/spice-v2.1/chain/work/polarres_wp3_cmip_CNRM/post/yearly/IVTu/IVTu_2008010100-2008123123.ncz /work/aa0049/a271109/spice-v2.1/chain/work/polarres_wp3_cmip_CNRM/post/yearly/IVTu/IVTu_2009010100-2009123123.ncz  /work/aa0238/a271093/scratch/mergedIVTu_2008_2009.nc
Mergetime /work/aa0049/a271109/spice-v2.1/chain/work/polarres_wp3_cmip_CNRM/post/yearly/IVTv/IVTv_2008010100-2008123123.ncz /work/aa0049/a271109/spice-v2.1/chain/work/polarres_wp3_cmip_CNRM/post/yearly/IVTv/IVTv_2009010100-2009123123.ncz  /work/aa0238/a271093/scratch/mergedIVTv_2008_2009.nc


In [45]:
f= xr.open_dataset('/work/aa0238/a271093/scratch/ObjectMasks_test_2009_07_01-2010_01_01.nc')




f.rlat.values

array([[-24.2, -24.2, -24.2, ..., -24.2, -24.2, -24.2],
       [-24.1, -24.1, -24.1, ..., -24.1, -24.1, -24.1],
       [-24. , -24. , -24. , ..., -24. , -24. , -24. ],
       ...,
       [ 33.7,  33.7,  33.7, ...,  33.7,  33.7,  33.7],
       [ 33.8,  33.8,  33.8, ...,  33.8,  33.8,  33.8],
       [ 33.9,  33.9,  33.9, ...,  33.9,  33.9,  33.9]], dtype=float32)

In [16]:
Tracking_functions.moaap.var_Area

NameError: name 'Tracking_functions' is not defined

In [ ]:

      )

 
The provided variables allow tracking the following phenomena
 
|  phenomenon  | tracking |
---------------------------
   Jetstream   |   no
   PSL CY/ACY  |   no
   Z500 CY/ACY |   no
   COLs        |   no
   IVT ARs     |   yes
   MS ARs      |   no
   Fronts      |   no
   TCs         |   no
   MCSs        |   no
   Equ. Waves  |   no
---------------------------
 
======> track IVT streams and atmospheric rivers (ARs)
        20915 object found
        break up long living IVT objects that have many elements


100%|██████████| 1502/1502 [28:51<00:00,  1.15s/it] 


        00:31:54.39
            Loop over 3651 objects


/work/aa0238/a271093/Scripts/MOAAP/Tracking_Functions.py:247: RuntimeWarning: All-NaN slice encountered
  obj_min = np.nanmin(data_slice, axis=(1, 2))
/work/aa0238/a271093/Scripts/MOAAP/Tracking_Functions.py:248: RuntimeWarning: All-NaN slice encountered
  obj_max = np.nanmax(data_slice, axis=(1, 2))
/work/aa0238/a271093/Scripts/MOAAP/Tracking_Functions.py:249: RuntimeWarning: Mean of empty slice
  obj_mean = np.nanmean(data_slice, axis=(1, 2))
/sw/spack-levante/mambaforge-22.9.0-2-Linux-x86_64-kptncg/lib/python3.10/site-packages/scipy/ndimage/_measurements.py:1407: RuntimeWarning: invalid value encountered in double_scalars
  results = [sum(input * grids[dir].astype(float), labels, index) / normalizer


        check if MSs quallify as ARs


/work/aa0238/a271093/Scripts/MOAAP/Tracking_Functions.py:3832: RuntimeWarning: divide by zero encountered in double_scalars
  if DIST.max()/DIST.min() < AR_width_lenght_ratio:


In [ ]:
with open('/work/aa0238/a271093/results/MOAAP/IVT_Tracking/CNRM_control_test/IVT_MOAPP_ICON_control_CNRMforc_100and85controlperc_remapped_3x_1984_01_01-1984_07_01_corrected.pkl', 'rb') as pickle_file:
    IVT1 = pickle.load(pickle_file)

#with open('/work/aa0238/a271093/scratch/IVT_test_2009_07_01-2010_01_01_corrected.pkl', 'rb') as pickle_file:
#    IVT2 = pickle.load(pickle_file)
    

In [47]:
IVT1.keys()

{'mass_center_loc': array([[11.96256684, 15.85561497],
        [12.15686275, 16.03921569],
        [11.97297297, 15.91441441],
        [11.83884298, 15.88016529],
        [11.66153846, 15.66923077],
        [11.54092527, 15.38434164],
        [11.55704698, 15.17114094],
        [11.78456592, 15.88424437],
        [12.15243902, 16.57317073],
        [12.28      , 16.32      ],
        [12.65705128, 16.36858974],
        [12.89285714, 16.14935065],
        [13.17320261, 16.0620915 ],
        [13.77257525, 16.07023411],
        [14.14900662, 16.13576159],
        [14.91694352, 16.55149502],
        [15.43581081, 16.40540541],
        [16.16607774, 16.45936396],
        [17.21771218, 16.94095941],
        [18.15830116, 16.62934363],
        [19.19838057, 16.50607287],
        [20.20600858, 16.38197425],
        [21.49767442, 16.55348837],
        [22.65989848, 16.52791878],
        [23.81967213, 16.86885246],
        [25.0239521 , 16.71856287],
        [26.33802817, 16.95774648],
        [

In [32]:
IVT2.keys()

dict_keys(['15001', '15002', '15003', '15004', '15005', '15006', '15007', '15008', '15009', '15010', '15011', '15012', '15013', '15014', '15015', '15016', '15017', '15018', '15019', '15020', '15021', '15022', '15023', '15024', '15025', '15026', '15027', '15028', '15029', '15030', '15031', '15032', '15033', '15034', '15035', '15036', '15037', '15038', '15039', '15040', '15041', '15042', '15043', '15044', '15045', '15046', '15047', '15048', '15049', '15050', '15051', '15052', '15053', '15054', '15055', '15056', '15057', '15058', '15059', '15060', '15061', '15062', '15063', '15064', '15065', '15066', '15067', '15068', '15069', '15070', '15071', '15072', '15073', '15074', '15075', '15076', '15077', '15078', '15079', '15080', '15081', '15082', '15083', '15084', '15085', '15086', '15087', '15088', '15089', '15090', '15091', '15092', '15093', '15094', '15095', '15096', '15097', '15098', '15099', '15100', '15101', '15102', '15103', '15104', '15105', '15106', '15107', '15108', '15109', '15110',

In [9]:
set(IVT.keys()).difference(set(IVT_cor.keys()))

{'1378',
 '1379',
 '1380',
 '1381',
 '1382',
 '1489',
 '1490',
 '1491',
 '1492',
 '1493',
 '1494',
 '1495',
 '1496',
 '1497',
 '1498',
 '1499',
 '1500',
 '1501',
 '1502',
 '1503',
 '1504',
 '1505',
 '1506',
 '1507',
 '1508',
 '1509',
 '1510',
 '1511',
 '1512',
 '1513',
 '1514',
 '1515',
 '1516',
 '1517',
 '1518',
 '1519',
 '1520',
 '1521',
 '1522',
 '1523',
 '1524',
 '1525',
 '1526',
 '1527',
 '1528',
 '1529',
 '1530',
 '1531',
 '1532',
 '1533',
 '1534',
 '1535',
 '1536',
 '1537',
 '1538',
 '1539',
 '1540',
 '1541',
 '1542',
 '1543',
 '1544',
 '1545',
 '1546',
 '1547',
 '1548',
 '1549',
 '1550',
 '1551',
 '1552',
 '1553',
 '1554',
 '1555',
 '1556',
 '1557',
 '1558',
 '1559',
 '1560',
 '1561',
 '1562',
 '1563',
 '1564',
 '1565',
 '1566',
 '1567',
 '1568',
 '1569',
 '1570',
 '1571',
 '1572',
 '1573',
 '1574',
 '1575',
 '1576',
 '1577',
 '1578',
 '1579',
 '1580',
 '1581',
 '1582',
 '1583',
 '1584',
 '1585',
 '1586',
 '1587',
 '1588',
 '1589',
 '1590',
 '1591',
 '1592',
 '1593',
 '1594',
 

In [26]:
ds=xr.open_dataset('/work/aa0238/a271093/scratch/200801_test_ObjectMasks_test_dt-1h_MOAAP-masks.nc')

In [54]:
key = '15001'

ds = xr.Dataset(
    data_vars=dict(
        speed=(['size'], IVT2[key]['size']),
    ),
    coords=dict(
        times=IVT2['15001']['times']
    )
)

In [60]:
key = '15001'

ds = xr.Dataset(
    data_vars=dict(
        speed=IVT2[key]['size'],
        times=IVT2[key]['times']
    
    )
)

In [61]:
ds

<xarray.Dataset>
Dimensions:  (speed: 35, times: 35)
Coordinates:
  * speed    (speed) float64 2.309e+10 2.519e+10 ... 7.647e+09 3.084e+09
  * times    (times) datetime64[ns] 2009-07-01T01:00:00 ... 2009-07-02T11:00:00
Data variables:
    *empty*

In [10]:
def cleanup_dicts(output_path,
                  output_file_temp,
                  file_start_date,
                  file_end_date,
                  type_):
    
    output_name = f'{output_path}{type_}_{output_file_name_temp}_{get_datetime_str(file_start_date)}-{get_datetime_str(file_end_date)}'

    
    if file_end_date != last_processed_date:
        file_end_date = file_end_date - relativedelta.relativedelta(months=1)




    obj_dict = get_dict_from_pkl(output_name)
    dict_bak = dict(obj_dict)
    for i, key in enumerate(dict_bak.keys()):
        obj_start_date =  dict_bak[key]['times'][0]
        obj_end_date =  dict_bak[key]['times'][-1]
    
        if obj_start_date < file_end_date:
            continue
    
        if obj_start_date == file_start_date and obj_start_date!=last_processed_date:
            del obj_dict[key] 

        if obj_end_date > file_end_date and obj_start_date > file_end_date:
            del obj_dict[key]
    
    
    output_name = f'{output_path}{type_}_{output_file_name_temp}_{get_datetime_str(file_start_date)}-{get_datetime_str(file_end_date)}'

    save_dict_as_pkl(obj_dict, output_name= output_name+'_corrected')
        
        
def get_dict_from_pkl(output_name):

    with open(output_name+'.pkl', 'rb') as pickle_file:
        ob_dict = pickle.load(pickle_file)
    return ob_dict

def save_dict_as_pkl(dict_, output_name):
    
    with open(output_name+'.pkl', 'wb') as handle:
        pickle.dump(dict_, handle, protocol=pickle.HIGHEST_PROTOCOL)

[datetime.datetime(2008, 8, 1, 0, 0),
 datetime.datetime(2009, 2, 1, 0, 0),
 datetime.datetime(2009, 8, 1, 0, 0),
 datetime.datetime(2010, 2, 1, 0, 0)]

 
The provided variables allow tracking the following phenomena
 
|  phenomenon  | tracking |
---------------------------
   Jetstream   |   no
   PSL CY/ACY  |   no
   Z500 CY/ACY |   no
   COLs        |   no
   IVT ARs     |   yes
   MS ARs      |   no
   Fronts      |   no
   TCs         |   no
   MCSs        |   no
   Equ. Waves  |   no
---------------------------
 
======> track IVT streams and atmospheric rivers (ARs)
        12200 object found
        break up long living IVT objects that have many elements


100%|██████████| 817/817 [05:47<00:00,  2.35it/s]  


        00:06:39.74
            Loop over 2082 objects


/work/aa0238/a271093/Scripts/MOAAP/Tracking_Functions.py:247: RuntimeWarning: All-NaN slice encountered
  obj_min = np.nanmin(data_slice, axis=(1, 2))
/work/aa0238/a271093/Scripts/MOAAP/Tracking_Functions.py:248: RuntimeWarning: All-NaN slice encountered
  obj_max = np.nanmax(data_slice, axis=(1, 2))
/work/aa0238/a271093/Scripts/MOAAP/Tracking_Functions.py:249: RuntimeWarning: Mean of empty slice
  obj_mean = np.nanmean(data_slice, axis=(1, 2))
/sw/spack-levante/mambaforge-22.9.0-2-Linux-x86_64-kptncg/lib/python3.10/site-packages/scipy/ndimage/_measurements.py:1407: RuntimeWarning: invalid value encountered in double_scalars
  results = [sum(input * grids[dir].astype(float), labels, index) / normalizer


        check if MSs quallify as ARs


/work/aa0238/a271093/Scripts/MOAAP/Tracking_Functions.py:3832: RuntimeWarning: divide by zero encountered in double_scalars
  if DIST.max()/DIST.min() < AR_width_lenght_ratio:


            Loop over 2081 objects
        00:10:09.33
 
Save the object masks into a joint netCDF
Saved: /work/aa0238/a271093/scratch/200801_test_2008_01_01_2008_08_01__ObjectMasks_test_2008_01_01_2008_08_01__dt-1h_MOAAP-masks.nc
        00:03:58.23
change of  year included -> merge files
Mergetime /work/aa0049/a271109/spice-v2.1/chain/work/polarres_wp3_cmip_CNRM/post/yearly/IVTu/IVTu_2008010100-2008123123.ncz /work/aa0049/a271109/spice-v2.1/chain/work/polarres_wp3_cmip_CNRM/post/yearly/IVTu/IVTu_2009010100-2009123123.ncz  /work/aa0238/a271093/scratch/mergedIVTu_2008_2009.nc


AttributeError: 'DataLoader' object has no attribute 'file_name_merged'

{'1': {'mass_center_loc': array([[ 68.83411602,  80.56892265],
         [ 67.76523796,  82.5470359 ],
         [ 66.81414198,  84.38862493],
         [ 66.73270697,  86.08891612],
         [ 67.49378399,  88.31131831],
         [ 67.25970448,  90.78975707],
         [ 66.9017341 ,  92.5867667 ],
         [ 67.44319001,  94.06281528],
         [ 68.84122368,  95.06921019],
         [ 69.8547568 ,  96.22322537],
         [ 70.83383118,  97.32536785],
         [ 72.27912016,  98.53732799],
         [ 73.92774566,  99.66623849],
         [ 75.84447273, 100.78007638],
         [ 77.68827718, 101.91391221],
         [ 79.58601235, 102.99787098],
         [ 81.69126005, 103.81769437],
         [ 84.21672963, 104.36492175],
         [ 87.34899989, 104.57722155],
         [ 91.00779163, 104.30153606],
         [ 95.28428132, 103.68471446],
         [ 99.098353  , 102.99778063],
         [103.33807702, 101.97213585],
         [108.09982509, 100.56884058],
         [113.42331045,  98.77283527],
 